In [1]:
import jieba
import re
import torch
from torch.autograd import Variable
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

# 数值运算和绘图的程序包
import numpy as np
import matplotlib.pyplot as plt
import matplotlib


# 加载机器学习的软件包
from sklearn.decomposition import PCA

#加载Word2Vec的软件包
import gensim as gensim
from gensim.models import Word2Vec
from gensim.models.keyedvectors import KeyedVectors
from gensim.models.word2vec import LineSentence


In [2]:
with open("红楼梦.txt",encoding='utf-8') as f:
    text = f.read()
print(text)

temp = jieba.lcut(text)
words = []
# print(temp)
for i in temp:
    #过滤掉所有的标点符号
    i = re.sub("[\s+\.\!\/_,$%^*(+\"\'””《》]+|[+——！，。？、~@#￥%……&*（）：]+", "", i)
    if len(i) > 0:
        words.append(i)
# print(len(words))
# print(words)
trigrams = [([words[i], words[i + 1]], words[i + 2]) for i in range(len(words) - 2)]
# 打印出前三个元素看看
print(trigrams[:3])

Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\Violet\AppData\Local\Temp\jieba.cache


《红楼梦》查看《红楼梦》书评和最新更新以及相关书籍推荐请到《红楼梦》专题网址http://www.xiabook.com/gudai/744/ 
下书网  http://www.xiabook.com，最有文艺气息的文学网站，提供经典的文学名著、武侠小说、言情小说、人文社科类书籍在线阅读，所有TXT电子书手机免费下载阅读，我们提供给您的小说不求最多，但求最经典最完整
 第一回　甄士隐梦幻识通灵　贾雨村风尘怀闺秀
    此开卷第一回也。作者自云：因曾历过一番梦幻之后，故将真事隐去，而借“通灵”之说，撰此《石头记》一书也。故曰“甄士隐”云云。但书中所记何事何人？自又云：“今风尘碌碌，一事无成，忽念及当日所有之女子，一一细考较去，觉其行止见识皆出于我之上。何我堂堂须眉，诚不若彼裙钗哉？实愧则有馀，悔又无益之大无可如何之日也！当此，则自欲将已往所赖天恩祖德，锦衣纨袴之时，饫甘餍肥之日，背父兄教育之恩，负师友规训之德，以至今日一技无成，半生潦倒之罪，编述一集，以告天下人：我之罪固不免，然闺阁中本自历历有人，万不可因我之不肖，自护己短，一并使其泯灭也。虽今日之茅椽蓬牖，瓦灶绳床，其晨夕风露，阶柳庭花，亦未有妨我之襟怀笔墨者。虽我未学，下笔无文，又何妨用假语村言，敷演出一段故事来，亦可使闺阁昭传，复可悦世之目，破人愁闷，不亦宜乎？”故曰“贾雨村云云。
    此回中凡用“梦”用“幻”等字，是提醒阅者眼目，亦是此书立意本旨。
    列位看官：你道此书从何而来？说起根由虽近荒唐，细按则深有趣味。待在下将此来历注明，方使阅者了然不惑。
    原来女娲氏炼石补天之时，于大荒山无稽崖炼成高经十二丈，方经二十四丈顽石三万六千五百零一块。娲皇氏只用了三万六千五百块，只单单剩了一块未用，便弃在此山青埂峰下。谁知此石自经煅炼之后，灵性已通，因见众石俱得补天，独自己无材不堪入选，遂自怨自叹，日夜悲号惭愧。
    一日，正当嗟悼之际，俄见一僧一道远远而来，生得骨格不凡，丰神迥异，说说笑笑来至峰下，坐于石边高谈快论。先是说些云山雾海神仙玄幻之事，后便说到红尘中荣华富贵；此石听了，不觉打动凡心，也想要到人间去享一享这荣华富贵，但自恨粗蠢，不得已，便口吐人言，向那僧道说道：“大师，弟子蠢物，不能见礼了。适闻二位谈那人世间荣耀繁华，心切慕之。弟子质虽粗蠢，性却稍通；况见二师仙形道体，定非凡品，必有补天

Loading model cost 0.530 seconds.
Prefix dict has been built successfully.


[(['红楼梦', '查看'], '红楼梦'), (['查看', '红楼梦'], '书评'), (['红楼梦', '书评'], '和')]


In [3]:
# 得到词汇表
vocab = set(words)
print(len(vocab))
# 两个字典，一个根据单词索引其编号，一个根据编号索引单词
#word_to_idx中的值包含两部分，一部分为id，另一部分为单词出现的次数
#word_to_idx中的每一个元素形如：{w:[id, count]}，其中w为一个词，id为该词的编号，count为该单词在words全文中出现的次数
word_to_idx = {} 
idx_to_word = {}
ids = 0
 
#对全文循环，构件这两个字典
for w in words:
    cnt = word_to_idx.get(w, [ids, 0])
    if cnt[1] == 0:
        ids += 1
    cnt[1] += 1
    word_to_idx[w] = cnt
    idx_to_word[ids] = w

45507


**`模型结构如下：`**<br>
1.输入层：embedding层，这一层的作用是：先将输入单词的编号映射为一个one hot编码的向量，形如：001000，维度为单词表大小。 然后，embedding会通过一个线性的神经网络层映射到这个词的向量表示，输出为embedding_dim<br>
2.线性层，从embedding_dim维度到128维度，然后经过非线性ReLU函数<br>
3.线性层：从128维度到单词表大小维度，然后log softmax函数，给出预测每个单词的概率

In [4]:
with open("红楼梦.txt",encoding='utf-8') as f:
    text = f.read()
# print(text)
temp = jieba.lcut(text)
words = []
print("temp:",temp)
#print(temp)
for i in temp:
    #过滤掉所有的标点符号
    i = re.sub("[\s+\.\!\/_,$%^*(+\"\'””《》]+|[+——！，。？、~@#￥%……&*（）：]+", "", i)
    if len(i) > 0:
        words.append(i)
print("len(words):",len(words))
print("words",words)
trigrams = [([words[i], words[i + 1]], words[i + 2]) for i in range(len(words) - 2)]
# 打印出前三个元素看看
print("前三个元素：",trigrams[:3])
# # 得到词汇表
# 

temp: ['《', '红楼梦', '》', '查看', '《', '红楼梦', '》', '书评', '和', '最新更新', '以及', '相关', '书籍', '推荐', '请', '到', '《', '红楼梦', '》', '专题', '网址', 'http', ':', '/', '/', 'www', '.', 'xiabook', '.', 'com', '/', 'gudai', '/', '744', '/', ' ', '\n', '下书网', ' ', ' ', 'http', ':', '/', '/', 'www', '.', 'xiabook', '.', 'com', '，', '最有', '文艺', '气息', '的', '文学', '网站', '，', '提供', '经典', '的', '文学名著', '、', '武侠小说', '、', '言情小说', '、', '人文', '社科类', '书籍', '在线', '阅读', '，', '所有', 'TXT', '电子书', '手机', '免费', '下载', '阅读', '，', '我们', '提供', '给', '您', '的', '小说', '不求', '最多', '，', '但求', '最', '经典', '最', '完整', '\n', ' ', '第一回', '\u3000', '甄士隐', '梦幻', '识通灵', '\u3000', '贾雨村', '风尘', '怀', '闺秀', '\n', ' ', ' ', ' ', ' ', '此', '开卷', '第一回', '也', '。', '作者', '自云', '：', '因曾', '历过', '一番', '梦幻', '之后', '，', '故', '将', '真事', '隐去', '，', '而', '借', '“', '通灵', '”', '之', '说', '，', '撰此', '《', '石头记', '》', '一书', '也', '。', '故曰', '“', '甄士隐', '”', '云云', '。', '但书中', '所记', '何事', '何人', '？', '自又云', '：', '“', '今', '风尘碌碌', '，', '一事无成', '，', '忽', '念及', '当日', '所有', '之

In [9]:
vocab = set(words)
print(len(vocab))
# # 两个字典，一个根据单词索引其编号，一个根据编号索引单词
# #word_to_idx中的值包含两部分，一部分为id，另一部分为单词出现的次数
# #word_to_idx中的每一个元素形如：{w:[id, count]}，其中w为一个词，id为该词的编号，count为该单词在words全文中出现的次数
word_to_idx = {}
idx_to_word = {}
ids = 0
#
# #对全文循环，构件这两个字典
for w in words:
   cnt = word_to_idx.get(w, [ids, 0])
   if cnt[1] == 0:
        ids += 1
   cnt[1] += 1
   word_to_idx[w] = cnt#     idx_to_word[ids] = w
print(word_to_idx["甄士隐"])



45507
[52, 11]


In [11]:
class NGram(nn.Module):

    def __init__(self, vocab_size, embedding_dim, context_size):
        super(NGram, self).__init__()
        self.embeddings = nn.Embedding(vocab_size, embedding_dim)  # 嵌入层
        self.linear1 = nn.Linear(context_size * embedding_dim, 128)  # 线性层
        self.linear2 = nn.Linear(128, vocab_size)  # 线性层

    def forward(self, inputs):
         # 嵌入运算，嵌入运算在内部分为两步：将输入的单词编码映射为one hot向量表示，然后经过一个线性层得到单词的词向量
        embeds = self.embeddings(inputs).view(1, -1)
         # 线性层加ReLU
        out = F.relu(self.linear1(embeds))

         # 线性层加Softmax
        out = self.linear2(out)
        log_probs = F.log_softmax(out)
        return log_probs

    def extract(self, inputs):
        embeds = self.embeddings(inputs)
        return embeds
losses = []  # 纪录每一步的损失函数
criterion = nn.NLLLoss()  # 运用负对数似然函数作为目标函数（常用于多分类问题的目标函数）
model = NGram(len(vocab), 10, 2).cuda()  # 定义NGram模型，向量嵌入维数为10维，N（窗口大小）为2
optimizer = optim.SGD(model.parameters(), lr=0.001)  # 使用随机梯度下降算法作为优化器
# # 循环100个周期
for epoch in range(100):
    total_loss = torch.Tensor([0])
    for context, target in trigrams:
         # 准备好输入模型的数据，将词汇映射为编码
        context_idxs = [word_to_idx[w][0] for w in context]

         # 包装成PyTorch的Variable
        context_var = Variable(torch.LongTensor(context_idxs))

         # 清空梯度：注意PyTorch会在调用backward的时候自动积累梯度信息，故而每隔周期要清空梯度信息一次。
        optimizer.zero_grad()

         # 用神经网络做计算，计算得到输出的每个单词的可能概率对数值
        log_probs = model(context_var)

         # 计算损失函数，同样需要把目标数据转化为编码，并包装为Variable
        loss = criterion(log_probs, Variable(torch.LongTensor([word_to_idx[target][0]])))

         # 梯度反传
        loss.backward()

         # 对网络进行优化
        optimizer.step()

         # 累加损失函数值
        total_loss += loss.data
    losses.append(total_loss)
    print('第{}轮，损失函数为：{:.2f}'.format(epoch, total_loss.numpy()[0]))
 # 从训练好的模型中提取每个单词的向量
vec = model.extract(Variable(torch.LongTensor([v[0] for v in word_to_idx.values()]))).cuda()
vec = vec.data.numpy()


#利用PCA算法进行降维
X_reduced = PCA(n_components=2).fit_transform(vec)
#
#
# 绘制所有单词向量的二维空间投影
fig = plt.figure(figsize = (30, 20))
ax = fig.gca()
ax.set_facecolor('black')
ax.plot(X_reduced[:, 0], X_reduced[:, 1], '.', markersize = 1, alpha = 0.4, color = 'white')
#
#
# # 绘制几个特殊单词的向量
words = ['贾宝玉', '林黛玉', '甄士隐', '贾雨村', '晴雯', '芙蓉花', '牡丹花', '薛宝钗', '王熙凤', '平儿', '贾母', '中秋节']
#
# # 设置中文字体，否则无法在图形上显示中文
zhfont1 = matplotlib.font_manager.FontProperties(fname='./华文仿宋.ttf', size=16)
for w in words:
    if w in word_to_idx:
        ind = word_to_idx[w][0]
        xy = X_reduced[ind]
        plt.plot(xy[0], xy[1], '.', alpha =1, color = 'red')
        plt.text(xy[0], xy[1], w, fontproperties = zhfont1, alpha = 1, color = 'white')



C:\Users\Violet\AppData\Local\Temp\ipykernel_18960\213163829.py:17: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  log_probs = F.log_softmax(out)


In [ ]:
#
f = open("红楼梦.txt", encoding='utf-8')
f = f.read().split("。")
print(list(f))
lines = []
for line in f:
    temp = jieba.lcut(line)
    words = []
    for i in temp:
      #过滤掉所有的标点符号
        i = re.sub("[\s+\.\!\/_,$%^*(+\"\'””《》]+|[+——！，\- 。？、~@#￥%……&*（）：；‘]+", "", i)
        if len(i) > 0:
            words.append(i)
    if len(words) > 0:
        lines.append(words)
print(lines)
model = Word2Vec(lines, size = 20, window = 2 , min_count = 0)
renwu = model.wv.most_similar('林黛玉', topn = 20)
print(renwu)
rawWordVec = []
word2ind = {}
for i, w in enumerate(model.wv.vocab):
    rawWordVec.append(model[w])
    word2ind[w] = i
rawWordVec = np.array(rawWordVec)
X_reduced = PCA(n_components=2).fit_transform(rawWordVec)
# # 绘制星空图
# # 绘制所有单词向量的二维空间投影
fig = plt.figure(figsize = (15, 10))
ax = fig.gca()
ax.set_facecolor('black')
ax.plot(X_reduced[:, 0], X_reduced[:, 1], '.', markersize = 1, alpha = 0.3, color = 'white')
#
#
# # 绘制几个特殊单词的向量
words = ['贾宝玉', '林黛玉', '香菱', '贾政', '晴雯', '妙玉', '袭人', '薛宝钗', '王熙凤', '平儿', '贾母', '探春']
# # 设置中文字体，否则无法在图形上显示中文
zhfont1 = matplotlib.font_manager.FontProperties(fname='./华文仿宋.ttf', size=16)
for w in words:
    if w in word2ind:
        ind = word2ind[w]
        xy = X_reduced[ind]
        plt.plot(xy[0], xy[1], '.', alpha =1, color = 'red')
        plt.text(xy[0], xy[1], w, fontproperties = zhfont1, alpha = 1, color = 'yellow')
plt.show()

## word2vect进行模型训练

## 训练的时候需要把数据重新进行调整，变成句子进行输入

In [ ]:
f = open("红楼梦.txt", encoding='utf-8')
f = f.read().split("。")
print(list(f))
lines = []
for line in f:
    temp = jieba.lcut(line)
    words = []
    for i in temp:
        #过滤掉所有的标点符号
        i = re.sub("[\s+\.\!\/_,$%^*(+\"\'””《》]+|[+——！，\- 。？、~@#￥%……&*（）：；‘]+", "", i)
        if len(i) > 0:
            words.append(i)
    if len(words) > 0:
        lines.append(words)
print(lines)

## 输入模型，将图像转化为二维空间进行展示

In [ ]:
model = Word2Vec(lines, size = 20, window = 2 , min_count = 0)
renwu = model.wv.most_similar('林黛玉', topn = 20)
print(renwu)
rawWordVec = []
word2ind = {}
for i, w in enumerate(model.wv.vocab):
    rawWordVec.append(model[w])
    word2ind[w] = i
rawWordVec = np.array(rawWordVec)
X_reduced = PCA(n_components=2).fit_transform(rawWordVec)

### 然后绘制图像，并且展示把几个特殊人物，在图像中展现出来'贾宝玉', '林黛玉', '香菱', '贾政', '晴雯', '妙玉', '袭人', '薛宝钗', '王熙凤', '平儿', '贾母', '探春'

In [ ]:
# 绘制所有单词向量的二维空间投影
fig = plt.figure(figsize = (15, 10))
ax = fig.gca()
ax.set_facecolor('black')
ax.plot(X_reduced[:, 0], X_reduced[:, 1], '.', markersize = 1, alpha = 0.3, color = 'white')
 
 
# 绘制几个特殊单词的向量
words = ['贾宝玉', '林黛玉', '香菱', '贾政', '晴雯', '妙玉', '袭人', '薛宝钗', '王熙凤', '平儿', '贾母', '探春']
# 设置中文字体，否则无法在图形上显示中文
zhfont1 = matplotlib.font_manager.FontProperties(fname='./华文仿宋.ttf', size=16)
for w in words:
    if w in word2ind:
        ind = word2ind[w]
        xy = X_reduced[ind]
        plt.plot(xy[0], xy[1], '.', alpha =1, color = 'red')
        plt.text(xy[0], xy[1], w, fontproperties = zhfont1, alpha = 1, color = 'yellow')
plt.show()